In [34]:
import os
import shutil

In [35]:
!sudo apt-get install git-lfs tree

In [36]:
!pip install datasets transformers

You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


In [37]:
!pip install https://github.com/kpu/kenlm/archive/master.zip pyctcdecode

  Using cached https://github.com/kpu/kenlm/archive/master.zip (542 kB)
  Preparing metadata (setup.py) ... done
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


In [38]:
from huggingface_hub import notebook_login

notebook_login()

In [39]:
!git config --global credential.helper store

In [40]:
!sudo apt install build-essential cmake libboost-system-dev libboost-thread-dev libboost-program-options-dev libboost-test-dev libeigen3-dev zlib1g-dev libbz2-dev liblzma-dev

E: Could not open lock file /var/lib/dpkg/lock-frontend - open (13: Permission denied)
E: Unable to acquire the dpkg frontend lock (/var/lib/dpkg/lock-frontend), are you root?


In [28]:
!wget -O - https://kheafield.com/code/kenlm.tar.gz | tar xz

--2022-05-26 13:39:11--  https://kheafield.com/code/kenlm.tar.gz
Resolving kheafield.com (kheafield.com)... 35.196.63.85
Connecting to kheafield.com (kheafield.com)|35.196.63.85|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 491888 (480K) [application/x-gzip]
Saving to: ‘STDOUT’

-                   100%[===================>] 480.36K   845KB/s    in 0.6s    

2022-05-26 13:39:12 (845 KB/s) - written to stdout [491888/491888]



In [9]:
!mkdir kenlm/build && cd kenlm/build && cmake .. && make -j2
!ls kenlm/build/bin

/bin/bash: cmake: command not found
ls: cannot access 'kenlm/build/bin': No such file or directory


In [10]:
import re

from datasets import load_dataset

username = "hf-test"  # change to your username
target_lang = "sv"

regex_chars_to_ignore = '[,?.!\-\;\:\"“%‘”�—’…–]'

dataset_1 = load_dataset("hf-test/sv_corpora_parliament_processed", split="train")
dataset_2 = load_dataset("mozilla-foundation/common_voice_9_0", "sv-SE", split="train+validation", use_auth_token=True)
dataset_3 = load_dataset("swedish_reviews", split="train+validation+test")

def clean_text(text):
  return re.sub(regex_chars_to_ignore, "", text.lower()) \
      .replace("\\\\punkt", "") \
      .replace("\\\\komma", "") \
      .replace("è", "e") \
      .replace("é", "e") \
      .replace("î", "i") \
      .replace("ü", "u") \
      .replace("ÿ", "y") \
      .replace("ô", "o") \
      .replace("\\", "") \
      .replace("/", "") \
      .replace("|", "")

dataset_1_text_clean = clean_text(" ".join(dataset_1["text"]))
dataset_2_text_clean =  clean_text(" ".join(dataset_2["sentence"]))
dataset_3_text_clean =  clean_text(" ".join(dataset_3["text"]))

with open("text.txt", "w") as file:
  file.write(dataset_1_text_clean + " " + dataset_2_text_clean + " " + dataset_3_text_clean)

Downloading:   0%|          | 0.00/1.16k [00:00<?, ?B/s]

Using custom data configuration hf-test--swedish_corpora_parliament_processed-93bdb791339208fb


Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Dataset parquet downloaded and prepared to /workspace/.cache/huggingface/datasets/hf-test___parquet/hf-test--swedish_corpora_parliament_processed-93bdb791339208fb/0.0.0/0b6d5799bb726b24ad7fc7be720c170d8e497f575d02d47537de9a5bac074901. Subsequent calls will reuse this data.


Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/sv-SE/9.0.0/26f54721b57ee2f31a333b315ed9151fbd8e693a3983c295fef63c67a12b9bf7)


Generating test split:   0%|          | 0/20697 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/20696 [00:00<?, ? examples/s]

Generating train split:   0%|          | 0/62089 [00:00<?, ? examples/s]

Dataset swedish_reviews downloaded and prepared to /workspace/.cache/huggingface/datasets/swedish_reviews/plain_text/1.0.0/b5ca53a6d7b4004000f565882a5294e9d7c9f4b341a2aa226bcf08b8762f68f5. Subsequent calls will reuse this data.


In [11]:
!kenlm/build/bin/lmplz -o 5 <"text.txt" > "5gram.arpa"

/bin/bash: kenlm/build/bin/lmplz: No such file or directory


In [12]:
!head -20 5gram.arpa

In [13]:
with open("5gram.arpa", "r") as read_file, open("5gram_correct.arpa", "w") as write_file:
  has_added_eos = False
  for line in read_file:
    if not has_added_eos and "ngram 1=" in line:
      count=line.strip().split("=")[-1]
      write_file.write(line.replace(f"{count}", f"{int(count)+1}"))
    elif not has_added_eos and "<s>" in line:
      write_file.write(line)
      write_file.write(line.replace("<s>", "</s>"))
      has_added_eos = True
    else:
      write_file.write(line)

In [14]:
!head -20 5gram_correct.arpa

In [ ]:
from transformers import AutoProcessor

processor = AutoProcessor.from_pretrained("marinone94/xls-r-300m-sv-robust")

In [18]:
from huggingface_hub import Repository

repo = Repository(local_dir="xls-r-300m-sv-robust", clone_from="marinone94/xls-r-300m-sv-robust")

/workspace/xls-r-300m-sv-robust/xls-r-300m-sv-robust is already a clone of https://huggingface.co/marinone94/xls-r-300m-sv-robust. Make sure you pull the latest changes with `repo.git_pull()`.


In [19]:
vocab_dict = processor.tokenizer.get_vocab()
sorted_vocab_dict = {k.lower(): v for k, v in sorted(vocab_dict.items(), key=lambda item: item[1])}

In [20]:
from pyctcdecode import build_ctcdecoder

decoder = build_ctcdecoder(
    labels=list(sorted_vocab_dict.keys()),
    kenlm_model_path="5gram_correct.arpa",
    alpha=0.5,
    beta=1.5,
)

Loading the LM will be faster if you build a binary file.
Reading /workspace/xls-r-300m-sv-robust/5gram_correct.arpa
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100


OSError: Cannot read model '5gram_correct.arpa' (End of file Byte: 0)

In [20]:
from transformers import Wav2Vec2ProcessorWithLM

processor_with_lm = Wav2Vec2ProcessorWithLM(
    feature_extractor=processor.feature_extractor,
    tokenizer=processor.tokenizer,
    decoder=decoder
)

In [21]:
lm_dir = "xls-r-300m-sv-robust/language_model"
if os.path.exists(lm_dir):
  shutil.rmtree(lm_dir)
processor_with_lm.save_pretrained("xls-r-300m-sv-robust")

In [22]:
!tree -h xls-r-300m-sv-robust/

xls-r-300m-sv-robust/
├── [  23]  added_tokens.json
├── [ 404]  all_results.json
├── [ 223]  alphabet.json
├── [2.2K]  config.json
├── [ 38K]  eda.ipynb
├── [4.6K]  eval.py
├── [ 228]  eval_results.json
├── [ 38K]  join_datasets_asr_ctc.py
├── [1.2K]  join_datasets_asr_ctc_run.sh
├── [4.0K]  language_model
│   ├── [4.5G]  5gram_correct.arpa
│   ├── [  79]  attrs.json
│   └── [5.8M]  unigrams.txt
├── [221K]  log_mozilla-foundation_common_voice_8_0_sv-SE_test_predictions.txt
├── [222K]  log_mozilla-foundation_common_voice_8_0_sv-SE_test_targets.txt
├── [ 12K]  log_speech-recognition-community-v2_dev_data_sv_validation_predictions.txt
├── [ 12K]  log_speech-recognition-community-v2_dev_data_sv_validation_targets.txt
├── [  50]  mozilla-foundation_common_voice_8_0_sv-SE_test_eval_results.txt
├── [ 285]  prepare_dataset_lm.py
├── [ 260]  preprocessor_config.json
├── [1.2G]  pytorch_model.bin
├── [3.1K]  README.md
├── [1.6K]  README_TEMPLATE.md
├── [  74]  requirements.txt
├── [ 207]  run_ev

In [23]:
!kenlm/build/bin/build_binary xls-r-300m-sv-robust/language_model/5gram_correct.arpa xls-r-300m-sv-robust/language_model/5gram.bin

Reading xls-r-300m-sv-robust/language_model/5gram_correct.arpa
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
****************************************************************************************************
SUCCESS


In [24]:
!rm xls-r-300m-sv-robust/language_model/5gram_correct.arpa && tree -h xls-r-300m-sv-robust/

xls-r-300m-sv-robust/
├── [  23]  added_tokens.json
├── [ 404]  all_results.json
├── [ 223]  alphabet.json
├── [2.2K]  config.json
├── [ 38K]  eda.ipynb
├── [4.6K]  eval.py
├── [ 228]  eval_results.json
├── [ 38K]  join_datasets_asr_ctc.py
├── [1.2K]  join_datasets_asr_ctc_run.sh
├── [4.0K]  language_model
│   ├── [2.0G]  5gram.bin
│   ├── [  79]  attrs.json
│   └── [5.8M]  unigrams.txt
├── [221K]  log_mozilla-foundation_common_voice_8_0_sv-SE_test_predictions.txt
├── [222K]  log_mozilla-foundation_common_voice_8_0_sv-SE_test_targets.txt
├── [ 12K]  log_speech-recognition-community-v2_dev_data_sv_validation_predictions.txt
├── [ 12K]  log_speech-recognition-community-v2_dev_data_sv_validation_targets.txt
├── [  50]  mozilla-foundation_common_voice_8_0_sv-SE_test_eval_results.txt
├── [ 285]  prepare_dataset_lm.py
├── [ 260]  preprocessor_config.json
├── [1.2G]  pytorch_model.bin
├── [3.1K]  README.md
├── [1.6K]  README_TEMPLATE.md
├── [  74]  requirements.txt
├── [ 207]  run_eval_cv.sh


In [25]:
!git config --global user.email "marinone94@gmail.com"
repo.push_to_hub(commit_message="Upload 5-gram lm-boosted decoder")

To https://huggingface.co/marinone94/xls-r-300m-sv-robust
   fc97a76..7f44855  main -> main



'https://huggingface.co/marinone94/xls-r-300m-sv-robust/commit/7f448551468d2896a8605cc133b844d92149b0d9'

In [26]:
cd xls-r-300m-sv-robust/

/content/xls-r-300m-sv-robust


In [27]:
!git status

On branch main
Your branch is up to date with 'origin/main'.

nothing to commit, working tree clean
